<table class="tfo-notebook-buttons" align="center">
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/PracticalDL/Practical-Deep-Learning-Book/blob/master/code/chapter-5/3-tf-explain.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/PracticalDL/Practical-Deep-Learning-Book/blob/master/code/chapter-5/3-tf-explain.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View source on GitHub</a>
  </td>
</table>

# `tf-explain`

tf-explain (by Raphael Meudec) helps understand the results and inner workings of a neural network with the help of visualizations, removing the veil on bias in our datasets. Few different visualization approaches are available with tf.explain.

- Grad CAM: The Gradient-weighted Class Activation Mapping visualizes how parts of the image affect the neural network's output by looking into the activation maps. A heatmap is generated based on the gradients of the object id from the last convolutional layer. Grad CAM is largely a broad-spectrum heatmap generator as it is robust to noise and can be used on an array of CNN models. 
- Activations: Visualize the activations for the convolutional layers. 
- Occlusion Sensitivity: Occludes a part of the image (using a small square patch placed randomly) to figure out how robust the network is. If the prediction is still correct, on average, the network is robust. The area in the image that is the warmest (i.e. red) has the most effect on the prediction when occluded.

In this notebook we will produce different visualizations on the sample images.

Note: After executing the first cell you may have to `RESTART RUNTIME` if you are running on Google Colab.

In [1]:
# Perform all installations
!pip install tensorflow-gpu==2.0.0
!pip install tf-explain==0.1.0

     |████████████████████████████████| 380.8MB 43kB/s 
     |████████████████████████████████| 450kB 39.8MB/s 
     |████████████████████████████████| 3.8MB 37.7MB/s 
     |████████████████████████████████| 51kB 6.5MB/s 
  Created wheel for gast: filename=gast-0.2.2-cp36-none-any.whl size=7542 sha256=42aecc33855e74f7caa2e06fe8c1592c8a6c68eb18c9f505293995db92fde5c3
  Stored in directory: /root/.cache/pip/wheels/5c/2e/7e/a1d4d4fcebe6c381f378ce7743a3ced3699feb89bcfbdadadd
Successfully built gast
ERROR: tensorflow 2.3.0 has requirement gast==0.3.3, but you'll have gast 0.2.2 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement tensorboard<3,>=2.3.0, but you'll have tensorboard 2.0.2 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement tensorflow-estimator<2.4.0,>=2.3.0, but you'll have tensorflow-estimator 2.0.1 which is incompatible.
ERROR: tensorflow-probability 0.11.0 has requirement gast>=0.3.2, but you'll have gast 0.2.2 which is incompatible.
  Found existing ins

In [4]:
import tensorflow as tf
import numpy as np

#Get TensorBoard to run
%load_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


We can add multiple types of callbacks while training or use its core API to generate TensorFlow events that can later be loaded into TensorBoard. 

In [5]:
from tf_explain.core.grad_cam import GradCAM
from tf_explain.core.occlusion_sensitivity import OcclusionSensitivity
from tf_explain.core.activations import ExtractActivations

In [6]:
For inference, all we need to do is pass an image, its ImageNet object ID along with a model into tf-explain’s functions. The object id is needed as tf.explain needs to figure out what is activated for that particular class.

SyntaxError: ignored

In [7]:
try:
  import google.colab
  IS_COLAB_ENV = True
except:
  IS_COLAB_ENV = False

In [8]:
def download_sample_image(filename):
    import requests
    url = f'https://raw.githubusercontent.com/PracticalDL/Practical-Deep-Learning-Book/master/sample-images/{filename}'
    open(filename, 'wb').write(requests.get(url).content)

In [9]:
if IS_COLAB_ENV:
    IMAGE_PATHS = ['dog.jpg', 'cat.jpg']
    for each_filename in IMAGE_PATHS:
        download_sample_image(each_filename)
else:
    IMAGE_PATHS = [ '../../sample-images/dog.jpg', '../../sample-images/cat.jpg']

In [16]:
#get summary of VGG16 network
model = tf.keras.applications.vgg16.VGG16(weights='imagenet',
                                              include_top=True)
model.summary()

Model: "vgg16"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_12 (InputLayer)        [(None, 224, 224, 3)]     0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 224, 224, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 224, 224, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 112, 112, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 112, 112, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 112, 112, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 56, 56, 128)       0     

In [17]:
#get summary of MobileNEt network
model = tf.keras.applications.mobilenet.MobileNet(weights='imagenet',
                                                      include_top=True)
model.summary()

Model: "mobilenet_1.00_224"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_13 (InputLayer)        [(None, 224, 224, 3)]     0         
_________________________________________________________________
conv1_pad (ZeroPadding2D)    (None, 225, 225, 3)       0         
_________________________________________________________________
conv1 (Conv2D)               (None, 112, 112, 32)      864       
_________________________________________________________________
conv1_bn (BatchNormalization (None, 112, 112, 32)      128       
_________________________________________________________________
conv1_relu (ReLU)            (None, 112, 112, 32)      0         
_________________________________________________________________
conv_dw_1 (DepthwiseConv2D)  (None, 112, 112, 32)      288       
_________________________________________________________________
conv_dw_1_bn (BatchNormaliza (None, 112, 112, 32

In [18]:
#get summary of RestNet50 network
model = tf.keras.applications.resnet50.ResNet50(weights='imagenet',
                                                    include_top=True)
model.summary()

Model: "resnet50"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_14 (InputLayer)           [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
conv1_pad (ZeroPadding2D)       (None, 230, 230, 3)  0           input_14[0][0]                   
__________________________________________________________________________________________________
conv1_conv (Conv2D)             (None, 112, 112, 64) 9472        conv1_pad[0][0]                  
__________________________________________________________________________________________________
conv1_bn (BatchNormalization)   (None, 112, 112, 64) 256         conv1_conv[0][0]                 
___________________________________________________________________________________________

In [ ]:
indices = [263, 281]

layers_name = ['activation_6']

for i in range(len(IMAGE_PATHS)):
    each_path = IMAGE_PATHS[i]
    index = indices[i]

    img = tf.keras.preprocessing.image.load_img(each_path,
                                                target_size=(224, 224))
    img = tf.keras.preprocessing.image.img_to_array(img)
    data = ([img], None)
    # Define name with which to save the result as
    name = each_path.split("/")[-1].split(".jpg")[0]


    #----------------------------------------------
    # For VGG16 Classifier CNN model
    #Save the Grad Cam visualization
    explainer = GradCAM()
    model = tf.keras.applications.vgg16.VGG16(weights='imagenet',
                                              include_top=True)
    grid = explainer.explain(data, model, 'block5_conv3', index)
    explainer.save(grid, '.', name + 'grad_cam_VGG16.png')

    #>>> new stuff
     # Compute Occlusion Sensitivity for patch_size 20
    explainer = OcclusionSensitivity()
    grid = explainer.explain(data, model, index, 20)
    explainer.save(grid, '.', name + 'occlusion_sensitivity_20_VGG16.png')
    # Compute Occlusion Sensitivity for patch_size 10
    grid = explainer.explain(data, model, index, 10)
    explainer.save(grid, '.', name + 'occlusion_sensitivity_10_VGG16.png')

    # Save the Activations visualizations
    data = (np.array([img]), None)
    explainer = ExtractActivations()
    #conv1 does not work for name of VGG16
    #grid = explainer.explain(data, model, ['conv1'])
    #explainer.save(grid, '.', name + 'activations_VGG16.png')


    #---------------------------------------
    #For ResNet50 Classifier CNN model
    # Save the Occlusion Sensitivity visualization
    explainer = OcclusionSensitivity()
    model = tf.keras.applications.resnet50.ResNet50(weights='imagenet',
                                                    include_top=True)
    # Compute Occlusion Sensitivity for patch_size 20
    grid = explainer.explain(data, model, index, 20)
    explainer.save(grid, '.', name + 'occlusion_sensitivity_20_ResNet50.png')
    # Compute Occlusion Sensitivity for patch_size 10
    grid = explainer.explain(data, model, index, 10)
    explainer.save(grid, '.', name + 'occlusion_sensitivity_10_ResNet50.png')

    #>>>>>>> new stuff
    #Save the Grad Cam visualization , focused on layer conv5_block3_3_conv in ResNet50
    explainer = GradCAM()
    grid = explainer.explain(data, model, 'conv5_block3_3_conv', index)
    explainer.save(grid, '.', name + 'grad_cam_ResNet50.png')

    # Save the Activations visualizations
    data = (np.array([img]), None)
    explainer = ExtractActivations()
    grid = explainer.explain(data, model, ['conv1'])
    explainer.save(grid, '.', name + 'activations_ResNet50.png')


    #-----------------------------------------------
    #For MobileNet
    # Save the Activations visualizations
    data = (np.array([img]), None)
    explainer = ExtractActivations()
    model = tf.keras.applications.mobilenet.MobileNet(weights='imagenet',
                                                      include_top=True)
    grid = explainer.explain(data, model, ['conv1'])
    explainer.save(grid, '.', name + 'activations_MobileNet.png')
    print("MOBILENET")
    model.summary()
    #>>>>>> newstuff
     #Save the Grad Cam visualization --focused on layer conv_pw_13 in MobileNet
    explainer = GradCAM()
    grid = explainer.explain(data, model, 'conv_pw_13', index)
    explainer.save(grid, '.', name + 'grad_cam_MobileNet.png')
     # Compute Occlusion Sensitivity for patch_size 20
    explainer = OcclusionSensitivity()
    grid = explainer.explain(data, model, index, 20)
    explainer.save(grid, '.', name + 'occlusion_sensitivity_20_MobileNet.png')
    # Compute Occlusion Sensitivity for patch_size 10
    grid = explainer.explain(data, model, index, 10)
    explainer.save(grid, '.', name + 'occlusion_sensitivity_10_MobileNet.png')